# `swift_too` module

## Swift Resolve example - conversion of name of object into coordinates

### API version = 1.2 `swiftools` = 2.4

#### Author: Jamie A. Kennea (Penn State)

In [1]:
from swifttools.swift_too import Swift_Resolve, Resolve, ObsQuery, VisQuery, TOO

### Name Resolution

"Name resolution" is the process of looking up a target by name to find out it's coordinates. the Swift TOO API provides (as of `swifttools 2.3`) a method for performing this task called `Swift_Resolve`, although for most cases you won't actually need to call this class by itself. `Swift_Resolve` essentially queries online name resolvers for a given name. We can demonstrate the usage as follows:

In [2]:
Swift_Resolve(name="LMC X-3")

Swift_Resolve(username='anonymous',name='LMC X-3')

So here we see that the RA / Dec value has been returned for RA/Dec based on the Simbad database (http://simbad.u-strasbg.fr/simbad/). We can also query more recent transients by querying transient brokers for coordinates such as TNS (https://www.wis-tns.org) and MARS (https://mars.lco.global). The choice of name resolver is automatic, so for example:

In [3]:
Resolve(name="AT2018cow")

Swift_Resolve(username='anonymous',name='AT2018cow')

Firstly, for `swifttools 2.3` we have introduced shorthand names for these classes, no longer do you need to include the `Swift_` prefix, so just `Resolve` works.

You can see that for "The Cow" the name has been resolved using TNS. This is because it recognizes that names starting with AT originate with TNS. This is useful for recent transients as Simbad often will not include them until results have been published. E.g. 

In [4]:
Resolve(name="AT2022aaa")

Swift_Resolve(username='anonymous',name='AT2022aaa')

For ZTF sources, MARS, which is a broker for ZTF transients, is used.

In [5]:
res = Resolve(name="ZTF20aasoapr")
res

Swift_Resolve(username='anonymous',name='ZTF20aasoapr')

We can as well as `ra` and `dec` attributes, use the `skycoord` attribute to return a astropy SkyCoord for the location. Note this will only work if you have `astropy` installed, and if you don't the next line will cause an error.

In [6]:
res.skycoord

<SkyCoord (FK5: equinox=J2000.000): (ra, dec) in deg
    (172.9475431, -25.727119)>

This is of course useful if you want to do things like convert to different formats, e.g.

In [7]:
res.skycoord.galactic

<SkyCoord (Galactic): (l, b) in deg
    (281.27179256, 33.77254096)>

### Using Swift_Resolve in API queries

Note that in order to use the RA/Dec of a source in API queries, we can simply pass the `ra`, `dec` or `skycoord` to the API query, for example:

In [8]:
VisQuery(ra=res.ra, dec=res.dec, length=7)

Swift_VisQuery(username='anonymous',ra='172.9475431',dec='-25.727119',length='7.0',begin='2022-03-28 16:56:12.678360')

In [9]:
VisQuery(skycoord=res.skycoord, length=7)

Swift_VisQuery(username='anonymous',ra='172.9475431',dec='-25.727119',length='7.0',begin='2022-03-28 16:56:12.678360')

### Using Swift_Resolve automatically

However, for most cases you will not want to have to generate a stand alone `Swift_Resolve` instance, as for API calls as of `swifttools 2.3` you can simply pass the `name` parameter, and it will automatically look up the RA/Dec. Here is an example using `Swift_ObsQuery`:

In [10]:
obs = ObsQuery(name="AT2018ahz")
obs

Swift_AFST(username='anonymous',ra='215.959340833',dec='-9.38821416667',radius='0.19666666666666668')

In this case, the `Swift_Resolve` call was generated automatically, and the results passed into the `Swift_ObsQuery` class. You can get the results of that call by looking at the `resolve` attribute:

In [11]:
obs.resolve

Swift_Resolve(username='anonymous',name='AT2018ahz')

In [12]:
obs.skycoord

<SkyCoord (FK5: equinox=J2000.000): (ra, dec) in deg
    (215.95934083, -9.38821417)>

### Use in `Swift_TOO` 

For `Swift_TOO` requests, the `source_name` parameter does not autoresolve, so if you wish to resolve names for a TOO request, simply issue a `Swift_Resolve` (or `Resolve` using shorthand introduced in `swifttools 2.3`. The following shows the most compact form of doing this. Note that for Resolve, as `name` is the first argument, you can leave out the `name=` keyword in the arguments.

In [13]:
too = TOO(skycoord=Resolve("Crab").skycoord)
print(f"RA/Dec(J2000) = {too.skycoord.to_string(style='hmsdms')}")

RA/Dec(J2000) = 05h34m31.9474s +22d00m52.153s


Or course, you can still set the values of RA/Dec manually.

In [14]:
too.ra = 83.633
too.dec = 22.015
print(f"RA/Dec(J2000) = {too.skycoord.to_string(style='hmsdms')}")

RA/Dec(J2000) = 05h34m31.92s +22d00m54s
